##### Copyright 2019 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# tf.data を使って NumPy データをロードする

<table class="tfo-notebook-buttons" align="left">
  <td><a target="_blank" href="https://www.tensorflow.org/tutorials/load_data/numpy"><img src="https://www.tensorflow.org/images/tf_logo_32px.png">TensorFlow.org で実行</a></td>
  <td>     <a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ja/tutorials/load_data/numpy.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png">Google Colabで実行</a> </td>
  <td><a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ja/tutorials/load_data/numpy.ipynb">     <img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png">     GitHubでソースを表示</a></td>
  <td><a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/ja/tutorials/load_data/numpy.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png">ノートブックをダウンロード</a></td>
</table>

このチュートリアルでは、NumPy 配列から `tf.data.Dataset` にデータを読み込む例を示します。

この例では、MNIST データセットを `.npz` ファイルから読み込みますが、 NumPy 配列がどこに入っているかは重要ではありません。


## 設定

In [2]:
 
import numpy as np
import tensorflow as tf

2024-01-11 17:59:40.945859: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-01-11 17:59:40.945907: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-01-11 17:59:40.947469: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


### `.npz` ファイルからのロード

In [3]:
DATA_URL = 'https://storage.googleapis.com/tensorflow/tf-keras-datasets/mnist.npz'

path = tf.keras.utils.get_file('mnist.npz', DATA_URL)
with np.load(path) as data:
  train_examples = data['x_train']
  train_labels = data['y_train']
  test_examples = data['x_test']
  test_labels = data['y_test']

    8192/11490434 [..............................] - ETA: 0s

 8396800/11490434 [====================>.........] - ETA: 0s

11490434/11490434 [==============================] - 0s 0us/step


## `tf.data.Dataset` を使って NumPy 配列をロード

サンプルの配列と対応するラベルの配列があるとします。 `tf.data.Dataset.from_tensor_slices` にこれら2つの配列をタプルとして入力し、`tf.data.Dataset` を作成します。

In [4]:
train_dataset = tf.data.Dataset.from_tensor_slices((train_examples, train_labels))
test_dataset = tf.data.Dataset.from_tensor_slices((test_examples, test_labels))

## データセットの使用

### データセットのシャッフルとバッチ化

In [5]:
BATCH_SIZE = 64
SHUFFLE_BUFFER_SIZE = 100

train_dataset = train_dataset.shuffle(SHUFFLE_BUFFER_SIZE).batch(BATCH_SIZE)
test_dataset = test_dataset.batch(BATCH_SIZE)

### モデルの構築と訓練

In [6]:
model = tf.keras.Sequential([
    tf.keras.layers.Flatten(input_shape=(28, 28)),
    tf.keras.layers.Dense(128, activation='relu'),
    tf.keras.layers.Dense(10)
])

model.compile(optimizer=tf.keras.optimizers.RMSprop(),
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['sparse_categorical_accuracy'])

In [7]:
model.fit(train_dataset, epochs=10)

Epoch 1/10


I0000 00:00:1704995986.474491   29733 device_compiler.h:186] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


  1/938 [..............................] - ETA: 13:45 - loss: 148.7183 - sparse_categorical_accuracy: 0.0625

 23/938 [..............................] - ETA: 2s - loss: 32.8734 - sparse_categorical_accuracy: 0.5924    

 47/938 [>.............................] - ETA: 1s - loss: 20.8201 - sparse_categorical_accuracy: 0.7048

...

866/938 [==========================>...] - ETA: 0s - loss: 0.1657 - sparse_categorical_accuracy: 0.9756

890/938 [===========================>..] - ETA: 0s - loss: 0.1634 - sparse_categorical_accuracy: 0.9759

912/938 [============================>.] - ETA: 0s - loss: 0.1630 - sparse_categorical_accuracy: 0.9759

936/938 [============================>.] - ETA: 0s - loss: 0.1616 - sparse_categorical_accuracy: 0.9762

938/938 [==============================] - 2s 2ms/step - loss: 0.1614 - sparse_categorical_accuracy: 0.9762


In [8]:
model.evaluate(test_dataset)

  1/157 [..............................] - ETA: 21s - loss: 0.0522 - sparse_categorical_accuracy: 0.9688

 29/157 [====>.........................] - ETA: 0s - loss: 0.6363 - sparse_categorical_accuracy: 0.9494 

 58/157 [==========>...................] - ETA: 0s - loss: 0.6640 - sparse_categorical_accuracy: 0.9520

 87/157 [===============>..............] - ETA: 0s - loss: 0.6731 - sparse_categorical_accuracy: 0.9499

116/157 [=====================>........] - ETA: 0s - loss: 0.5986 - sparse_categorical_accuracy: 0.9562

145/157 [==========================>...] - ETA: 0s - loss: 0.5345 - sparse_categorical_accuracy: 0.9589

157/157 [==============================] - 0s 2ms/step - loss: 0.5400 - sparse_categorical_accuracy: 0.9591


[0.5399600267410278, 0.9591000080108643]